## NPL Project Notebook

#### Libraries, Imports and Data

In [60]:
import csv # csv reader
import nltk
from sklearn.svm import LinearSVC
from sklearn.svm import SVC
from nltk.classify import SklearnClassifier
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from nltk.tag import pos_tag
from nltk.chunk import tree2conlltags
from random import shuffle
from sklearn.pipeline import Pipeline
from sklearn import metrics as Skmet #used for precision_recall_fscore_support()
from operator import itemgetter #used to unpack turples
import re
import math
import multiprocessing
#from gensim.models import Word2Vec
#from gensim.models import KeyedVectors
import time
import numpy as np

import warnings
warnings.filterwarnings('ignore')

nltk.download("wordnet", "c:/nltk_data/")
nltk.download('stopwords', "c:/nltk_data/")

[nltk_data] Downloading package wordnet to c:/nltk_data/...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to c:/nltk_data/...
[nltk_data]   Package stopwords is already up-to-date!


True

#### Preprocessing and Data Loading

In [61]:
def parseData(dataLine):
    line = dataLine[0]     
    character = dataLine[1] 
    gender = dataLine[2]   
    return (line, character, gender)

def parseContractions(dataLine):
    contraction = dataLine[0]     
    expansion = dataLine[1]  
    return (contraction.lower(), expansion.lower())

def preProcess(text):
    # Should return a list of tokens
    text = text.lower() #normalize the text 
    text = re.sub(r"\"", "", text) # speach mark removal.
    
    tokenizer = RegexpTokenizer(r"[']?\w+[']?\w?\w?\w?\w?\w?") # splits sent into words maintain  " ' " to allow for later expansion.
    tokenizedTemp = tokenizer.tokenize(text)
    lemmatizer = WordNetLemmatizer()
    stopWords = set(stopwords.words('english')) #stop word removal.
    
    contractionExpandedTemp = []
    for w in tokenizedTemp:
        contemp = contractions.get(w)
        if  contemp != None:
            tempContract = contractions[w] #getting contraction dictionary value
            expandedContraction = tempContract.split(" ") #splits expanded cotnractions then adds it to the processed text.
            contractionExpandedTemp.extend(expandedContraction);
        else:
            contractionExpandedTemp.append(w)
    
    #processedTemp = []
    #for w in contractionExpandedTemp: #stop word removal and lemmatization
    #    if (w not in stopWords) or w == "": # removes stop words and blank strings
    #        processedTemp.append(w)   
    
    taggedTemp = nltk.pos_tag(contractionExpandedTemp)
    grammar = "NP: {<DT>?<JJ>*<NN>}" #nltk documentation.
        
    if taggedTemp:
        cp = nltk.RegexpParser(grammar)
        result = cp.parse(taggedTemp)
        tagged = tree2conlltags(result) #converts a tree to a series of turples.
        print(tagged)
        return tagged
    else:
        return None
    
    
def loadData(path, Text=None):
    with open(path,encoding='utf8') as f:
        reader = csv.reader(f, delimiter=',')
        for line in reader:
            (line, character, gender) = parseData(line)
            temp = preProcess(line)
            if temp: #removes empty lines
                rawData.append((line, character, gender));  
                preprocessedData.append((temp, character, gender))

def loadContractions(path):
    with open(path,encoding='utf8') as f:
        reader = csv.reader(f, delimiter='\t')
        for line in reader:
            (contraction, expansion) = parseContractions(line)
            contractions[contraction] = expansion
            
def splitData(percentage): #splits the data into 4 sets
    dataSamples = len(rawData)
    halfOfData = int(len(rawData)/2)
    trainingSamples = int((percentage*dataSamples)/2)
    for (line, character, gender) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
        trainDataBinary.append((toFeatureVector(preProcess(line)),gender))
    
    for (line, character, gender) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
        testDataBinary.append((toFeatureVector(preProcess(line)),gender))
        
    for (line, character, gender) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
        trainDataMulti.append((toFeatureVector(preProcess(line)),character))
    
    for (line, character, gender) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
        testDataMulti.append((toFeatureVector(preProcess(line)),character))
        
def toFeatureVector(tokens):
    lineDict = {} # Should return a dictionary containing features as keys, and weights as values
    for token in tokens: #adding to the line dict
        if token in lineDict:
            lineDict[token] = lineDict[token] + 1
        else:
            lineDict[token] = 1
            
    for token in tokens: #adds values to featureDict
        if token in featureDict:
            featureDict[token] = featureDict[token] + 1
        else:
            featureDict[token] = 1
        
    return lineDict

def splitDataNER(percentage): #splits the data into 4 sets
    dataSamples = len(rawData)
    halfOfData = int(len(rawData)/2)
    trainingSamples = int((percentage*dataSamples)/2)
    for (line, character, gender) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
        temp = preProcess(line)
        if temp: #removes empty lines
            trainDataBinary.append((temp,gender))
            trainDataMulti.append((temp,character))
    
    for (line, character, gender) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
        temp = preProcess(line)
        if temp: #removes empty lines
            testDataBinary.append((temp,gender))
            testDataMulti.append((temp,character))



#### Training and Cross validation

In [62]:
def trainClassifier(trainData):
    print("Training Classifier...")
    pipeline =  Pipeline([('svc', LinearSVC())])
    return SklearnClassifier(pipeline).train(trainData)

def crossValidate(dataset, folds):
    shuffle(dataset)
    #print(dataset[0])
    cv_results = []
    temp = []
    totalPrecision = 0
    totalRecall = 0
    totalFScore = 0
    totalAccuracy = 0
    foldSize = int(len(dataset)/folds) #the fold size
    for i in range(0,len(dataset),foldSize):
        tempDataSet = dataset[0:i] + dataset[i+foldSize:len(dataset)] # joins to parts of the list to form the dataset to test.
        testingSet = dataset[i:i+foldSize] #takes the fold size an i to find the current test data.
        trueLabels = list(map(itemgetter(1), testingSet)) #creates a 1D array of result labels
        testingSetRemovedLabel = list(map(itemgetter(0),testingSet))
        
        #training
        classifier = trainClassifier(tempDataSet) #classifier using 9/10th of the dataset
        #classifing
        
        results = []
        for i in testingSetRemovedLabel:
            results.append(predictLabel(i,classifier))
        
        #print(results[0:10])        
        #print(trueLabels[0:10])
        
        precision = Skmet.precision_score(trueLabels, results,average='macro') #finds precision score
        #print(precision)
        recall = Skmet.recall_score(trueLabels, results,average='macro') #finds recall score
        #print(recall)
        f_score = 2 * (precision * recall)/(precision + recall) #calculates f_score
        #print(f_score)
        accuracy = Skmet.accuracy_score(trueLabels,results) #calculate accuracy
        #print(accuracy)
        totalPrecision += precision
        totalRecall += recall
        if math.isnan(f_score): #if f_score not a number won't add it to the total
            totalFScore += 0
        else:
            totalFScore += f_score
        totalAccuracy += accuracy
    
    cv_results = (totalPrecision/folds,totalRecall/folds,totalFScore/folds,totalAccuracy/folds)
        
    return cv_results

def predictLabels(lineSamples, classifier):
    return classifier.classify_many(map(lambda t: toFeatureVector(preProcess(t[1])), lineSamples))

def predictLabel(lineSample, classifier):
    return classifier.classify((lineSample))

#### Main

In [63]:
featureDict = {} # A global dictionary of features
contractions = {} #dictionary of english contractions
rawData = []          # the filtered data from the dataset file
preprocessedData = [] # the preprocessed reviews 
trainDataBinary = []   # the training data with the binary gender labels.
testDataBinary = [] # the test data currently 10% with the binary gender labels.
trainDataMulti = [] # the training data with the multi class name labels.
testDataMulti = [] # the test data currently 10% with the multi class name labels.

trainingDataSource = "training.csv"
testingDataSource = "test.csv"
contractionsPath = "contractions.txt"
loadContractions(contractionsPath)



print("Now %d rawData, %d trainData, %d testData, %d trainData, %d testData" % (len(rawData), len(trainDataMulti),
    len(testDataMulti),len(trainDataBinary), len(testDataBinary)),"Preparing the datasets...",sep='\n')

#populating preprocessedData and rawData
loadData(trainingDataSource)  

print("Now %d rawData, %d trainData, %d testData, %d trainData, %d testData" % (len(rawData), len(trainDataMulti),
    len(testDataMulti),len(trainDataBinary), len(testDataBinary)), "Preparing training and test data...",sep='\n')

splitDataNER(0.9)

# We print the number of training samples and the number of features
print("Now %d rawData, %d trainData, %d testData, %d trainData, %d testData" % (len(rawData), len(trainDataMulti),
      len(testDataMulti),len(trainDataBinary), len(testDataBinary)), "Training Samples: ", len(trainDataBinary), 
      "Features: ", len(featureDict), sep='\n')

crossValidationBinaryResults = crossValidate(trainDataBinary, 10)
print("Precision, Recall, Fscore, Accuracy")
print(crossValidationBinaryResults)

crossValidationMultiResults = crossValidate(trainDataMulti, 10)
print("Precision, Recall, Fscore, Accuracy")
print(crossValidationMultiResults)





Now 0 rawData, 0 trainData, 0 testData, 0 trainData, 0 testData
Preparing the datasets...
[('someone', 'NN', 'B-NP'), ('had', 'VBD', 'O'), ('fun', 'NN', 'B-NP')]
[('it', 'PRP', 'O'), ('is', 'VBZ', 'O'), ('no', 'DT', 'B-NP'), ('problem', 'NN', 'I-NP'), ('honestly', 'RB', 'O'), ('go', 'VB', 'O'), ('on', 'IN', 'O'), ('go', 'NN', 'B-NP'), ('and', 'CC', 'O'), ('open', 'VB', 'O'), ('the', 'DT', 'B-NP'), ('launderette', 'NN', 'I-NP'), ('leave', 'VBP', 'O'), ('it', 'PRP', 'O'), ('with', 'IN', 'O'), ('me', 'PRP', 'O')]
[('last', 'JJ', 'B-NP'), ('night', 'NN', 'I-NP'), ('was', 'VBD', 'O'), ('better', 'RBR', 'O'), ('than', 'IN', 'O'), ('ever', 'RB', 'O'), ('what', 'WP', 'O'), ('is', 'VBZ', 'O'), ('all', 'DT', 'O'), ('this', 'DT', 'B-NP'), ('anything', 'NN', 'I-NP'), ('interesting', 'JJ', 'O')]
[('have', 'VB', 'O'), ('you', 'PRP', 'O'), ('checked', 'VBN', 'O'), ('the', 'DT', 'B-NP'), ('answerphone', 'NN', 'I-NP'), ('any', 'DT', 'O'), ('calls', 'NNS', 'O')]
[("oscar's", 'JJ', 'B-NP'), ('asleep', 'N

[('well', 'RB', 'O'), ('that', 'IN', 'O'), ('sounds', 'VBZ', 'O'), ('great', 'JJ', 'B-NP'), ('i', 'NN', 'I-NP'), ('can', 'MD', 'O'), ('make', 'VB', 'O'), ('that', 'DT', 'O'), ('do', 'VBP', 'O'), ('you', 'PRP', 'O'), ('want', 'VB', 'O'), ('me', 'PRP', 'O'), ('to', 'TO', 'O'), ('bring', 'VB', 'O'), ('anything', 'NN', 'B-NP')]
[('abi', 'NN', 'B-NP'), ('is', 'VBZ', 'O'), ('everything', 'NN', 'B-NP'), ('okay', 'NN', 'B-NP')]
[('is', 'VBZ', 'O'), ('that', 'IN', 'O'), ('all', 'DT', 'O')]
[('why', 'WRB', 'O'), ('should', 'MD', 'O'), ('not', 'RB', 'O'), ('it', 'PRP', 'O'), ('be', 'VB', 'O'), ('has', 'VBZ', 'O'), ('someone', 'NN', 'B-NP'), ('been', 'VBN', 'O'), ('saying', 'VBG', 'O'), ('something', 'NN', 'B-NP'), ('cos', 'NNS', 'O'), ('if', 'IN', 'O'), ("someone's", 'JJ', 'O'), ('been', 'VBN', 'O'), ('saying', 'VBG', 'O'), ('something', 'NN', 'B-NP'), ('you', 'PRP', 'O'), ('should', 'MD', 'O'), ('not', 'RB', 'O'), ("'ve", 'VBP', 'O'), ('been', 'VBN', 'O'), ('listening', 'VBG', 'O')]
[('what', 'W

[("ﬁmum's", 'IN', 'O'), ('the', 'DT', 'B-NP'), ('wordﬂ', 'NN', 'I-NP'), ('see', 'VBP', 'O'), ('ya', 'RB', 'O'), ('later', 'RB', 'O')]
[('i', 'NNS', 'O'), ('do', 'VBP', 'O'), ('not', 'RB', 'O'), ('want', 'VB', 'O'), ('it', 'PRP', 'O'), ('to', 'TO', 'O'), ('be', 'VB', 'O'), ('like', 'IN', 'O'), ('this', 'DT', 'O')]
[('what', 'WP', 'O'), ('was', 'VBD', 'O'), ('he', 'PRP', 'O'), ('saying', 'VBG', 'O')]
[('i', 'NNS', 'O'), ('do', 'VBP', 'O'), ('not', 'RB', 'O'), ('think', 'VB', 'O'), ('we', 'PRP', 'O'), ('make', 'VBP', 'O'), ('the', 'DT', 'O'), ('most', 'RBS', 'O'), ('convincing', 'JJ', 'B-NP'), ('couple', 'NN', 'I-NP'), ('do', 'VBP', 'O'), ('you', 'PRP', 'O')]
[('you', 'PRP', 'O'), ('said', 'VBD', 'O'), ('i', 'NN', 'B-NP'), ('had', 'VBD', 'O'), ('never', 'RB', 'O'), ('get', 'VB', 'O'), ('married', 'JJ', 'B-NP'), ('i', 'NN', 'I-NP'), ('thought', 'VBD', 'O'), ('you', 'PRP', 'O'), ('had', 'VBD', 'O'), ('be', 'VB', 'O'), ('pleased', 'VBN', 'O')]
[("someone's", 'RB', 'O'), ('been', 'VBN', 'O'),

[('well', 'RB', 'O'), ('it', 'PRP', 'O'), ('is', 'VBZ', 'O'), ('a', 'DT', 'B-NP'), ('little', 'JJ', 'I-NP'), ('bit', 'NN', 'I-NP'), ('loose', 'JJ', 'O'), ('but', 'CC', 'O'), ('it', 'PRP', 'O'), ('is', 'VBZ', 'O'), ('nothing', 'NN', 'B-NP'), ('a', 'DT', 'B-NP'), ('belt', 'NN', 'I-NP'), ('will', 'MD', 'O'), ('not', 'RB', 'O'), ('sort', 'VB', 'O')]
[('so', 'RB', 'O'), ('what', 'WP', 'O'), ('did', 'VBD', 'O'), ('you', 'PRP', 'O'), ('do', 'VB', 'O'), ('last', 'JJ', 'O')]
[('oh', 'UH', 'O'), ('what', 'WP', 'O'), ('do', 'VBP', 'O'), ('not', 'RB', 'O'), ('you', 'PRP', 'O'), ('think', 'VBP', 'O'), ('i', 'NNS', 'O'), ('am', 'VBP', 'O'), ('up', 'RB', 'O'), ('to', 'TO', 'O'), ('it', 'PRP', 'O')]
[('shirley', 'NN', 'B-NP'), ('shirl', 'NN', 'B-NP'), ('shirl', 'NNS', 'O'), ('wake', 'VBP', 'O'), ('up', 'RP', 'O'), ('shirley', 'NN', 'B-NP')]
[('not', 'RB', 'O'), ('a', 'DT', 'B-NP'), ('lot', 'NN', 'I-NP')]
[('gives', 'VBZ', 'O'), ('you', 'PRP', 'O'), ('power', 'NN', 'B-NP'), ('keeps', 'VBZ', 'O'), ('him

[('like', 'IN', 'O'), ('i', 'NN', 'B-NP'), ('had', 'VBD', 'O'), ('notice', 'VBN', 'O'), ('with', 'IN', 'O'), ('this', 'DT', 'B-NP'), ('hangover', 'NN', 'I-NP'), ('you', 'PRP', 'O'), ('had', 'VBD', 'O'), ('be', 'VB', 'O'), ('doing', 'VBG', 'O'), ('me', 'PRP', 'O'), ('a', 'DT', 'B-NP'), ('favour', 'JJ', 'I-NP'), ('go', 'NN', 'I-NP'), ('ahead', 'RB', 'O')]
[('no', 'DT', 'O')]
[('yeah', 'RB', 'O'), ('well', 'RB', 'O'), ('yesterday', 'NN', 'B-NP'), ('was', 'VBD', 'O'), ('a', 'DT', 'B-NP'), ('bad', 'JJ', 'I-NP'), ('day', 'NN', 'I-NP'), ('were', 'VBD', 'O'), ('not', 'RB', 'O'), ('it', 'PRP', 'O'), ('i', 'JJ', 'O'), ('mean', 'VBP', 'O'), ('i', 'NN', 'B-NP'), ('had', 'VBD', 'O'), ('been', 'VBN', 'O'), ('drinking', 'VBG', 'O'), ('i', 'NN', 'B-NP'), ('was', 'VBD', 'O'), ('not', 'RB', 'O'), ('thinking', 'VBG', 'O'), ('straight', 'RB', 'O'), ('just', 'RB', 'O'), ('forget', 'VB', 'O'), ('about', 'IN', 'O'), ('it', 'PRP', 'O'), ('eh', 'VBZ', 'O'), ('start', 'RB', 'O'), ('again', 'RB', 'O'), ('please'

...

[('it', 'PRP', 'O'), ('is', 'VBZ', 'O'), ('a', 'DT', 'B-NP'), ('gift', 'NN', 'I-NP')]
[('you', 'PRP', 'O'), ('and', 'CC', 'O'), ('me', 'PRP', 'O'), ('we', 'PRP', 'O'), ('will', 'MD', 'O'), ('do', 'VB', 'O'), ('our', 'PRP$', 'O'), ('best', 'JJS', 'O'), ('yeah', 'NN', 'B-NP'), ('i', 'NN', 'B-NP'), ('will', 'MD', 'O'), ('be', 'VB', 'O'), ('free', 'JJ', 'O'), ('at', 'IN', 'O'), ('4', 'CD', 'O'), ('before', 'IN', 'O'), ('it', 'PRP', 'O'), ('gets', 'VBZ', 'O'), ('busy', 'JJ', 'O'), ('downstairs', 'NNS', 'O')]
[('i', 'NN', 'B-NP'), ('prefer', 'VBP', 'O'), ('ms', 'JJ', 'B-NP'), ('cross', 'NN', 'I-NP'), ('now', 'RB', 'O'), ('thank', 'VBZ', 'O'), ('you', 'PRP', 'O'), ('or', 'CC', 'O'), ('tanya', 'VB', 'O'), ('do', 'VBP', 'O'), ('not', 'RB', 'O'), ('call', 'VB', 'O'), ('me', 'PRP', 'O'), ('branning', 'VBG', 'O')]
[('and', 'CC', 'O'), ('let', 'VB', 'O'), ('lucy', 'JJR', 'O'), ('win', 'VB', 'O'), ('you', 'PRP', 'O'), ('have', 'VBP', 'O'), ('been', 'VBN', 'O'), ('looking', 'VBG', 'O'), ('forward', '

[('thanks', 'NNS', 'O'), ('for', 'IN', 'O'), ('letting', 'VBG', 'O'), ('me', 'PRP', 'O'), ('know', 'VBP', 'O'), ('most', 'JJS', 'O'), ('blokes', 'NNS', 'O'), ('would', 'MD', 'O'), ('not', 'RB', 'O'), ('have', 'VB', 'O'), ('you', 'PRP', 'O'), ('are', 'VBP', 'O'), ('such', 'JJ', 'O'), ('a', 'DT', 'B-NP'), ('gentleman', 'NN', 'I-NP')]
[('or', 'CC', 'O'), ('maybe', 'RB', 'O'), ('you', 'PRP', 'O'), ('did', 'VBD', 'O'), ('it', 'PRP', 'O')]
[('look', 'NN', 'B-NP'), ('i', 'NN', 'B-NP'), ('know', 'VBP', 'O'), ('it', 'PRP', 'O'), ('is', 'VBZ', 'O'), ('been', 'VBN', 'O')]
[('you', 'PRP', 'O'), ('thinking', 'VBG', 'O'), ('now', 'RB', 'O'), ('any', 'DT', 'O'), ('of', 'IN', 'O'), ('it', 'PRP', 'O'), ('hitting', 'VBG', 'O'), ('home', 'NN', 'B-NP')]
[('i', 'JJ', 'O'), ('mean', 'VBP', 'O'), ('it', 'PRP', 'O'), ('sean', 'VBZ', 'O'), ('our', 'PRP$', 'O'), ('secret', 'JJ', 'B-NP'), ('i', 'NN', 'I-NP'), ('am', 'VBP', 'O'), ('gonna', 'NN', 'B-NP'), ('go', 'VBP', 'O'), ('downstairs', 'NNS', 'O'), ('do', 'VBP

[('the', 'DT', 'B-NP'), ('thing', 'NN', 'I-NP'), ('is', 'VBZ', 'O'), ('i', 'JJ', 'B-NP'), ('cannot', 'NN', 'I-NP'), ('i', 'NNS', 'O'), ('have', 'VBP', 'O'), ('got', 'VBN', 'O'), ('to', 'TO', 'O'), ('do', 'VB', 'O'), ('something', 'NN', 'B-NP')]
[('well', 'RB', 'O'), ('that', 'DT', 'O'), ('was', 'VBD', 'O'), ('a', 'DT', 'B-NP'), ('nice', 'JJ', 'I-NP'), ('reception', 'NN', 'I-NP'), ('i', 'NN', 'B-NP'), ('mean', 'VBP', 'O'), ('anyone', 'NN', 'B-NP'), ('would', 'MD', 'O'), ('think', 'VB', 'O'), ('you', 'PRP', 'O'), ('were', 'VBD', 'O'), ('pleased', 'JJ', 'O'), ('to', 'TO', 'O'), ('see', 'VB', 'O'), ('me', 'PRP', 'O'), ('tan', 'VB', 'O')]
[('you', 'PRP', 'O'), ('do', 'VBP', 'O'), ('not', 'RB', 'O'), ('have', 'VB', 'O'), ('to', 'TO', 'O')]
[('oh', 'UH', 'O'), ('come', 'VBN', 'O'), ('on', 'IN', 'O'), ('no', 'DT', 'O'), ('strippers', 'NNS', 'O'), ('this', 'DT', 'B-NP'), ('time', 'NN', 'I-NP'), ('alright', 'NN', 'B-NP'), ('just', 'RB', 'O'), ('me', 'PRP', 'O'), ('and', 'CC', 'O'), ('you', 'PRP'

[('do', 'VB', 'O'), ('not', 'RB', 'O'), ('say', 'VB', 'O'), ('that', 'IN', 'O')]
[('who', 'WP', 'O'), ('is', 'VBZ', 'O'), ('that', 'IN', 'O')]
[('oi', 'IN', 'O'), ('we', 'PRP', 'O'), ('are', 'VBP', 'O'), ('going', 'VBG', 'O'), ('to', 'TO', 'O'), ('celebrate', 'VB', 'O'), ('and', 'CC', 'O'), ('that', 'DT', 'O'), ('is', 'VBZ', 'O'), ('that', 'IN', 'O')]
[('sorry', 'NN', 'B-NP'), ('is', 'VBZ', 'O'), ('this', 'DT', 'O'), ('working', 'VBG', 'O'), ('for', 'IN', 'O'), ('you', 'PRP', 'O'), ('cos', 'VBP', 'O'), ('my', 'PRP$', 'O'), ('thumbs', 'NNS', 'O'), ('are', 'VBP', 'O'), ('killing', 'VBG', 'O'), ('me', 'PRP', 'O')]
[('great', 'JJ', 'B-NP'), ('cannot', 'NN', 'I-NP'), ('wait', 'NN', 'B-NP'), ('to', 'TO', 'O'), ('show', 'VB', 'O'), ('you', 'PRP', 'O'), ('what', 'WP', 'O'), ('i', 'VB', 'O'), ('can', 'MD', 'O'), ('do', 'VB', 'O'), ('come', 'VB', 'O'), ('and', 'CC', 'O'), ('sit', 'VB', 'O'), ('down', 'RP', 'O')]
[('yeah', 'NN', 'B-NP')]
[('find', 'VB', 'O'), ('her', 'PRP$', 'O'), ('oh', 'NN', 'B

AttributeError: 'list' object has no attribute 'items'

#### Results

##### Here are the results on a simple SVM 
###### Binary (Gender)
Precision, Recall, Fscore, Accuracy
(0.552863688427898, 0.5525422108455417, 0.5527028606377715, 0.5524175824175823)
###### Multiclass (Name)
Precision, Recall, Fscore, Accuracy
(0.17559268036085093, 0.1614969298891055, 0.16823929530879572, 0.19098901098901097)
##### Results with the use of sentence vector averages features using word2vec (Defunct)
###### Binary (Gender)
Precision, Recall, Fscore, Accuracy
(0.26970308788598574, 0.55, 0.36155444681963606, 0.5394061757719715)
###### Multiclass (Name)
Precision, Recall, Fscore, Accuracy
(0.009647928213248879, 0.07555555555555557, 0.016884015118703227, 0.1216627078384798)  #poor
##### Here are the results with an addition of POS with stopword removal.
###### Binary (Gender)
Precision, Recall, Fscore, Accuracy
(0.5472277118296398, 0.5466568140554461, 0.5469418653347782, 0.5463736263736263)

###### Multiclass (Name)
Precision, Recall, Fscore, Accuracy
(0.1626678821084411, 0.15166406188712622, 0.15691284279441098, 0.18142857142857144)

##### Here are the results with an addition of POS without stopword removal.
###### Binary (Gender)
Precision, Recall, Fscore, Accuracy
(0.5472277118296398, 0.5466568140554461, 0.5469418653347782, 0.5463736263736263)

###### Multiclass (Name)
Precision, Recall, Fscore, Accuracy
(0.16033137908389353, 0.15353047359820343, 0.15683540884530806, 0.17824175824175828)


#### Defunct Word2Vec Methods

In [144]:
model = word2vecVocabandTraining(preprocessedData, word2vecInitModel())
splitDataW2V(0.9, model)

def predictLabelW2V(lineSample, classifier, word_vectors):
    temp = np.zeros(50)
    count = 0;
    for token in lineSample: #adding to the line dict
        if token in word_vectors:
            temp = temp + word_vectors[token]
            count += 1;

    if count > 0:
        lineVector = np.divide(temp, count)    
    else:
        lineVector = temp;
    return classifier.predict((lineVector.reshape(1, -1)))

def word2vecInitModel():
    cores = multiprocessing.cpu_count()
    word2vec = Word2Vec(min_count=10, #the kaggle tutorial used a much larger dataset 
                     window=2,
                     size=50,
                     sample=4e-6, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=20,
                     workers=cores-1)
    return word2vec

def word2vecVocabandTraining(dataset, model):
    t = time.time()
    datasetSansLabels = list(map(itemgetter(0),dataset))
    model.build_vocab(datasetSansLabels, progress_per=2000)
    print('Time to build vocab: {} mins'.format(round((time.time() - t) / 60, 2)))
    
    t = time.time();
    model.train(datasetSansLabels, total_examples=model.corpus_count, epochs=30, report_delay=1)
    print('Time to train the model: {} mins'.format(round((time.time() - t) / 60, 2)))
    return model

def crossValidateW2V(dataset, folds, model):
    shuffle(dataset)
    #print(dataset[0])
    cv_results = []
    temp = []
    totalPrecision = 0
    totalRecall = 0
    totalFScore = 0
    totalAccuracy = 0
    foldSize = int(len(dataset)/folds) #the fold size
    for i in range(0,len(dataset),foldSize):
        tempDataSet = dataset[0:i] + dataset[i+foldSize:len(dataset)] # joins to parts of the list to form the dataset to test.
        testingSet = dataset[i:i+foldSize] #takes the fold size an i to find the current test data.
        trueLabels = list(map(itemgetter(1), testingSet)) #creates a 1D array of result labels
        testingSetRemovedLabel = list(map(itemgetter(0),testingSet))
        
        #training
        classifier = trainClassifierW2V(tempDataSet) #classifier using 9/10th of the dataset
        #classifing
        
        results = []
        for i in testingSetRemovedLabel:
            results.append(predictLabelW2V(i,classifier,model))
        
        #print(results[0:10])        
        #print(trueLabels[0:10])
        
        precision = Skmet.precision_score(trueLabels, results,average='macro') #finds precision score
        #print(precision)
        recall = Skmet.recall_score(trueLabels, results,average='macro') #finds recall score
        #print(recall)
        f_score = 2 * (precision * recall)/(precision + recall) #calculates f_score
        #print(f_score)
        accuracy = Skmet.accuracy_score(trueLabels,results) #calculate accuracy
        #print(accuracy)
        totalPrecision += precision
        totalRecall += recall
        if math.isnan(f_score): #if f_score not a number won't add it to the total
            totalFScore += 0
        else:
            totalFScore += f_score
        totalAccuracy += accuracy
    
    cv_results = (totalPrecision/folds,totalRecall/folds,totalFScore/folds,totalAccuracy/folds)
        
    return cv_results

def trainClassifierW2V(trainData):
    print("Training Classifier... SVC on vectors")
    SVC = LinearSVC()
    X,Y = [ a for a,b in trainData ], [ b for a,b in trainData ]
    return SVC.fit(X,Y)

def splitDataW2V(percentage, model): #splits the data into 4 sets
    dataSamples = len(rawData)
    halfOfData = int(len(rawData)/2)
    trainingSamples = int((percentage*dataSamples)/2)
    for (line, character, gender) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
        temp = toFeatureVectorW2V(preProcess(line), model);
        if type(temp) is not int:
            trainDataBinary.append((temp, gender))
            trainDataMulti.append((temp, character))
    
    for (line, character, gender) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
        temp = toFeatureVectorW2V(preProcess(line), model);
        if type(temp) is not int:
            testDataBinary.append((temp, gender))
            testDataMulti.append((temp,character))

def toFeatureVectorW2V(tokens, word_vectors):
    lineVector = []
    temp = np.zeros(50)
    count = 0;
    for token in tokens: #adding to the line dict
        if token in word_vectors:
            temp = temp + word_vectors[token]
            count += 1;
    
    lineVector = -1
    if count > 0:
        lineVector = np.divide(temp, count)
    
    return lineVector

Time to build vocab: 0.0 mins
Time to train the model: 0.01 mins
